In [53]:
# !pip install assemblyai
# !pip install moviepy
# !pip install SpeechRecognition
# !pip install pysrt==1.1.2
# !pip install nltk
# !pip install nltk.tokenize
# import os
# import subprocess
# import speech_recognition as sr
# import pysrt
# import nltk
# from moviepy.editor import VideoFileClip
# from nltk.tokenize import PunktSentenceTokenizer

# # Download the necessary dataset for tokenization
# nltk.download('punkt')

# # Function to transcribe audio from the video using SpeechRecognition
# def transcribe_audio(video_path):
#     recognizer = sr.Recognizer()
#     transcript = ""

#     with VideoFileClip(video_path) as video:
#         audio_path = "audio.wav"
#         video.audio.write_audiofile(audio_path, codec='pcm_s16le')

#         audio = sr.AudioFile(audio_path)

#         with audio as source:
#             audio_data = recognizer.record(source)
#             try:
#                 transcript = recognizer.recognize_google(audio_data, language="ar")
#             except sr.UnknownValueError:
#                 print("Google Speech Recognition could not understand the audio.")
#             except sr.RequestError as e:
#                 print(f"Could not request results from Google Speech Recognition service: {e}")

#     os.remove(audio_path)
#     return transcript

# # Function to tokenize Arabic text into sentences using nltk
# def tokenize_into_sentences(text):
#     sentences = nltk.sent_tokenize(text, language='arabic')
#     return sentences

# # Function to generate SRT file with timestamps
# def generate_srt(video_path):
#     transcript = transcribe_audio(video_path)
#     sentences = tokenize_into_sentences(transcript)  # Tokenize transcript into sentences

#     # Calculate timestamps
#     start_time = 0
#     srt = pysrt.SubRipFile()

#     for i, sentence in enumerate(sentences):
#         end_time = start_time + 2  # Adjust as needed
#         srt_entry = pysrt.SubRipItem(index=i + 1, start=pysrt.SubRipTime(seconds=start_time), end=pysrt.SubRipTime(seconds=end_time), text=sentence.strip())
#         srt.append(srt_entry)
#         start_time = end_time

#     srt_file_path = os.path.splitext(video_path)[0] + ".srt"
#     srt.save(srt_file_path, encoding='utf-8')
#     print(f"SRT file saved to: {srt_file_path}")
# # Example usage
# video_path = "videoarabic.mp4"
# generate_srt(video_path)


!pip install moviepy==2.0.0.dev2
!pip install imageio==2.25.1

!pip install imagemagick

!cat /etc/ImageMagick-6/policy.xml | sed 's/none/read,write/g'> /etc/ImageMagick-6/policy.xml
!pip install pysrt==1.1.2
!pip install SpeechRecognition
import os
%pip install AssemblyAI
import assemblyai as aai
import cv2
import audioop
import tempfile
import speech_recognition as sr
def recognize_audio_segment(audio_file, start_time, end_time):
    recognizer = sr.Recognizer()
    with sr.AudioFile(audio_file) as source:
        audio_data = recognizer.record(source, offset=start_time, duration=end_time - start_time)
        try:
            text = recognizer.recognize_google(audio_data, language='ar')
            return text
        except sr.UnknownValueError:
            return ""
# Set your AssemblyAI API key
aai.settings.api_key = "fa08fc0604e44c31b52f69e79e280248"

# Initialize the transcriber
transcriber = aai.Transcriber()
video = VideoFileClip("videoarabicthree.mp4")

# Specify the path to your video file
video_path = "videoarabicthree.mp4"

# Extract the base name of the video file
video_base_name = os.path.splitext(os.path.basename(video_path))[0]
# Set the language globally for all transcription requests
# aai.settings.language('ar-AR')


# Transcribe the audio from the video
cap = cv2.VideoCapture(video_path)
fps = cap.get(cv2.CAP_PROP_FPS)
frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
duration = frame_count / fps
audio = video.audio

audio_file_path = os.path.splitext(video_path)[0] + ".wav"
audio.write_audiofile(audio_file_path, codec='pcm_s16le') 
# audio_file_path = 'temp_audio.wav'
    # Extract audio from the video
command = f'ffmpeg -i {video_path} -vn -acodec pcm_s16le -ar 44100 -ac 2 {audio_file_path}'
os.system(command)

# Create SRT object
srt = pysrt.SubRipFile()
segment_duration = 5  # Duration of audio segments in seconds

for i in range(0, int(duration), segment_duration):
        # Perform speech recognition on the audio segment
        recognized_text = recognize_audio_segment(audio_file_path, i, min(i + segment_duration, duration))
        start_time = i
        end_time = min(i + segment_duration, duration)
        srt_entry = pysrt.SubRipItem(index=len(srt) + 1, start=pysrt.SubRipTime(seconds=start_time), end=pysrt.SubRipTime(seconds=end_time), text=recognized_text)
        srt.append(srt_entry)

srt_file_path = os.path.splitext(video_path)[0] + ".srt"
srt.save(srt_file_path, encoding='utf-8')
print(f"SRT file saved to: {srt_file_path}")
# srt_file_path = f"{video_base_name}.srt"

# # Write the subtitles to the SRT file
# with open(srt_file_path, "w") as f:
#     f.write(srt_file_path)

# print(f"Subtitles saved to: {srt_file_path}")


# Place files in this path or modify the paths to point to where the files are
srtfilename = srt_file_path
mp4filename = "videoarabicthree.mp4"

import sys
import pysrt
from moviepy.editor import VideoFileClip, TextClip, CompositeVideoClip


def time_to_seconds(time_obj):
    return time_obj.hours * 3600 + time_obj.minutes * 60 + time_obj.seconds + time_obj.milliseconds / 1000


# def create_subtitle_clips(subtitles, videosize,fontsize=24, font='Arial', color='yellow', debug = False):
#     subtitle_clips = []

#     for subtitle in subtitles:
#         start_time = time_to_seconds(subtitle.start)
#         end_time = time_to_seconds(subtitle.end)
#         duration = end_time - start_time

#         video_width, video_height = videosize

#         text_clip = TextClip(subtitle.text, fontsize=fontsize, font=font, color=color, bg_color = 'black',size=(video_width*3/4, None), method='caption').set_start(start_time).set_duration(duration)
#         subtitle_x_position = 'center'
#         subtitle_y_position = video_height* 4 / 5

#         text_position = (subtitle_x_position, subtitle_y_position)
#         subtitle_clips.append(text_clip.set_position(text_position))

    # return subtitle_clips

def create_subtitle_clips(subtitles,videosize, fontsize=24, font='Arial', color='yellow', debug=False):
    subtitle_clips = []

    for subtitle in subtitles:
        start_time = time_to_seconds(subtitle.start)
        end_time = time_to_seconds(subtitle.end)
        duration = end_time - start_time

        try:
            video_width, video_height = videosize

            text_clip = TextClip(subtitle.text, fontsize=fontsize, font=font, color=color, bg_color='black',
                                 size=(video_width * 3 / 4, None), method='caption').set_start(start_time).set_duration(
                duration)
            subtitle_y_position = video_height* 4 / 5
            text_position = ('center', subtitle_y_position)  # Dynamically position subtitles at the bottom center
            subtitle_clips.append(text_clip.set_position(text_position))
        except Exception as e:
            if debug:
                print(f"Error processing subtitle '{subtitle.text}': {e}")

    return subtitle_clips


# Load video and SRT file
video = VideoFileClip(mp4filename)
subtitles = pysrt.open(srtfilename)

begin,end= mp4filename.split(".mp4")
output_video_file = begin+'_subtitled'+".mp4"

print ("Output file name: ",output_video_file)

# Create subtitle clips
subtitle_clips = create_subtitle_clips(subtitles,video.size)

# Add subtitles to the video
final_video = CompositeVideoClip([video] + subtitle_clips)

# Write output video file
final_video.write_videofile(output_video_file)


from IPython.display import HTML
from base64 import b64encode
mp4 = open(output_video_file,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)


ERROR: Could not find a version that satisfies the requirement imagemagick (from versions: none)
ERROR: No matching distribution found for imagemagick
'cat' is not recognized as an internal or external command,
operable program or batch file.



MoviePy - Writing audio in videoarabicthree.wav


MoviePy - Done.
SRT file saved to: videoarabicthree.srt
Output file name:  videoarabicthree_subtitled.mp4
Moviepy - Building video videoarabicthree_subtitled.mp4.
MoviePy - Writing audio in videoarabicthree_subtitledTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video videoarabicthree_subtitled.mp4



Moviepy - Done !
Moviepy - video ready videoarabicthree_subtitled.mp4
